In [1]:
import numpy as np
import pandas as pd
import random
import plotly.express as px
from yahoo_fin.stock_info import *
import matplotlib.pyplot as plt

In [2]:
basket = ['TLT', 'IEF', 'SPDN']
total_return_window = 90
volatility_window = 40
nlargest = 3

In [3]:
df_data = {}
for stock_ticker in basket: 
    data = get_data(stock_ticker)
    adj_closed = data['adjclose'][-total_return_window:]
    df_data[stock_ticker] = adj_closed
    
df = pd.DataFrame(df_data)
df = df.dropna()
df

TLT         IEF   SPDN
2021-08-17  147.936783  116.998940  15.23
2021-08-18  148.433731  116.939163  15.41
2021-08-19  149.526947  117.198189  15.39
2021-08-20  149.626358  117.088593  15.26
2021-08-23  149.526947  117.118484  15.13
...                ...         ...    ...
2021-12-16  149.139999  115.750000  14.36
2021-12-17  150.830002  116.010002  14.52
2021-12-20  149.699997  115.910004  14.67
2021-12-21  149.130005  115.449997  14.40
2021-12-22  149.820007  115.559998  14.27

[90 rows x 3 columns]

In [4]:
window_returns = np.log(df.iloc[-1]) - np.log(df.iloc[0])
nlargest = list(window_returns.nlargest(4).index)
nlargest

['TLT', 'IEF', 'SPDN']

In [5]:
returns = df[nlargest].pct_change()
returns_cov_normalized = returns[-volatility_window:].apply(lambda x: np.log(1+x)).cov()
returns_corr_normalized = returns[-volatility_window:].apply(lambda x: np.log(1+x)).corr()
returns_std = returns.apply(lambda x: np.log(1+x)).std()

In [6]:
#Returns Standard Deviations
returns_std


TLT     0.009463
IEF     0.003593
SPDN    0.008554
dtype: float64

In [7]:
#Returns Correlations
returns_corr_normalized

TLT       IEF      SPDN
TLT   1.000000  0.899999  0.468478
IEF   0.899999  1.000000  0.502179
SPDN  0.468478  0.502179  1.000000

In [8]:
#Returns Covariances 
returns_cov_normalized

TLT       IEF      SPDN
TLT   0.000116  0.000042  0.000049
IEF   0.000042  0.000018  0.000021
SPDN  0.000049  0.000021  0.000094

In [9]:
port_returns = []
port_volatility = []
port_weights = []

num_assets = len(returns.columns)
num_portfolios = 10000
individual_rets = window_returns[nlargest]

## Analyze custom portfolio weight
Keep it commented out when not in use

In [10]:
# for port in range(1): 
#     weights = [1,0,0,0]
#     port_weights.append(weights)
    
#     rets = np.dot(weights, individual_rets)
#     port_returns.append(rets)
    
#     var = returns_cov_normalized.mul(weights, axis=0).mul(weights, axis=1).sum().sum()
#     sd = np.sqrt(var)
#     ann_sd = sd * np.sqrt(256)
#     port_volatility.append(ann_sd)

## Analyze random portfolios and their efficient frontier

In [11]:
for port in range(num_portfolios): 
    weights = np.random.random(num_assets)
    weights = weights/np.sum(weights)
    port_weights.append(weights)
    
    rets = np.dot(weights, individual_rets)
    port_returns.append(rets)
    
    portfolio_var = returns_cov_normalized.mul(weights, axis=0).mul(weights, axis=1).sum().sum()
    sd = np.sqrt(portfolio_var)
    ann_sd = sd * np.sqrt(256)
    port_volatility.append(ann_sd)

## Build DataFrame of portfolios

In [12]:
    
data = {'Returns': port_returns, 'Volatility': port_volatility}
hover_data = []
for counter, symbol in enumerate(nlargest): 
    data[symbol] = [w[counter] for w in port_weights]
    hover_data.append(symbol)
    
portfolios_V1 = pd.DataFrame(data)
portfolios_V1.head()

Returns  Volatility       TLT       IEF      SPDN
0  0.006287    0.150370  0.795262  0.181240  0.023498
1  0.000273    0.142535  0.711015  0.191418  0.097567
2 -0.041089    0.107963  0.037448  0.400263  0.562289
3 -0.009159    0.119220  0.474259  0.361659  0.164082
4 -0.032796    0.135734  0.385849  0.043798  0.570353

## Efficient Frontier

In [13]:
import plotly.express as px
fig = px.scatter(portfolios_V1, x="Volatility", y="Returns", hover_data=hover_data)
fig.show()

## Min Variance Portfolio

In [14]:
min_var_portfolio = portfolios_V1.iloc[portfolios_V1['Volatility'].idxmin()]
min_var_portfolio

Returns      -0.012820
Volatility    0.069416
TLT           0.007787
IEF           0.980077
SPDN          0.012137
Name: 3866, dtype: float64

In [15]:
PORTFOLIO_VALUE = 35000
min_var_portfolio[nlargest] * PORTFOLIO_VALUE

TLT       272.533274
IEF     34302.678920
SPDN      424.787806
Name: 3866, dtype: float64

## Max Sharpe Ratio Portfolio

In [16]:
max_sharpe_portfolio = portfolios_V1.iloc[(portfolios_V1['Returns'] / portfolios_V1['Volatility']).idxmax()]
max_sharpe_portfolio

Returns       0.011734
Volatility    0.169914
TLT           0.974624
IEF           0.020063
SPDN          0.005313
Name: 1807, dtype: float64

In [17]:
max_sharpe_portfolio[nlargest] * PORTFOLIO_VALUE

TLT     34111.856791
IEF       702.197000
SPDN      185.946210
Name: 1807, dtype: float64